In [ ]:
import geopandas as gpd
import pandas as pd
import glob
from shapely.wkb import loads
import os

In [ ]:
# Set the directory containing Parquet files
directory = "Energy/"  # Change this to your folder

# List all Parquet files in the directory
parquet_files = [os.path.join(directory, f) for f in os.listdir(directory) if f.endswith('.parquet') and f != 'solar_new.parquet']

# List to store processed DataFrames
dataframes = []

# Process each Parquet file
for file in parquet_files:
    print(f"Processing: {file}")

    # Read the Parquet file
    data = pd.read_parquet(file)

    # Convert WKB geometry to Shapely
    data['geom'] = data['geometry'].apply(lambda x: loads(x))

    # Create obj_type column
    data['obj_type'] = data['generator:source'] + ' power generator'

    # Select relevant columns
    processed_data = pd.DataFrame(data[['id', 'obj_type', 'geom']])

    # Store DataFrame
    dataframes.append(processed_data)

# Merge all DataFrames
merged_data = pd.concat(dataframes, ignore_index=True)

Processing: Energy/battery.parquet
Processing: Energy/geo.parquet
Processing: Energy/hydro.parquet
Processing: Energy/tidal.parquet
Processing: Energy/wave.parquet
Processing: Energy/wind.parquet


In [ ]:
merged_data

id                 obj_type  \
0        node/7342664546  battery power generator   
1        node/8196015382  battery power generator   
2        node/8371124657  battery power generator   
3       node/10121875287  battery power generator   
4       node/10939320863  battery power generator   
...                  ...                      ...   
116246  node/12625544667     wind power generator   
116247  node/12625544668     wind power generator   
116248  node/12625544669     wind power generator   
116249  node/12625897353     wind power generator   
116250  node/12626056780     wind power generator   

                                 geom  
0        POINT (8.5179932 49.0180318)  
1        POINT (0.5218841 51.8530108)  
2        POINT (8.8740961 53.0589349)  
3       POINT (11.5945844 48.1894386)  
4        POINT (9.9642052 53.5279202)  
...                               ...  
116246  POINT (11.5098463 50.9010364)  
116247   POINT (11.5040723 50.896273)  
116248    POINT (11.5106877 50.89622)  
116249  POINT (-4.7896548 50.3559277)  
116250  POINT (-0.8096294 53.5682824)  

[116251 rows x 3 columns]

In [ ]:
merged_data['obj_type'].drop_duplicates()

0          battery power generator
103     geothermal power generator
153          hydro power generator
4817         tidal power generator
4853          wave power generator
4855          wind power generator
Name: obj_type, dtype: object

In [ ]:
data_solar = pd.read_parquet("Energy/solar_new.parquet")

In [ ]:
data_solar['geom'] = data_solar['geom'].apply(lambda x: loads(x))
data_solar_use = pd.DataFrame(data_solar[['id','obj_type','geom']])
data_solar_use

id               obj_type  \
0         node/845916353  solar power generator   
1        node/4625897593  solar power generator   
2        node/5667061969  solar power generator   
3        node/5703493122  solar power generator   
4        node/6364873921  solar power generator   
...                  ...                    ...   
607719  node/12628917768  solar power generator   
607720  node/12628917769  solar power generator   
607721  node/12628922141  solar power generator   
607722  node/12628922142  solar power generator   
607723  node/12628933024  solar power generator   

                                         geom  
0               POINT (-3.1934835 57.4876746)  
1               POINT (-2.0957238 57.1967122)  
2        POINT (-1.9431720000000001 57.34456)  
3                POINT (-2.817305 56.5880764)  
4               POINT (-3.9429175 56.1014206)  
...                                       ...  
607719          POINT (19.3732906 49.9230957)  
607720          POINT (19.3716505 49.9244208)  
607721          POINT (19.3361361 49.9016856)  
607722  POINT (19.3359857 49.901575199999996)  
607723          POINT (20.0109837 49.8862204)  

[607724 rows x 3 columns]

In [ ]:
merged_data_use = pd.concat([merged_data, data_solar_use], ignore_index=True)
merged_data_use

id                 obj_type  \
0        node/7342664546  battery power generator   
1        node/8196015382  battery power generator   
2        node/8371124657  battery power generator   
3       node/10121875287  battery power generator   
4       node/10939320863  battery power generator   
...                  ...                      ...   
723970  node/12628917768    solar power generator   
723971  node/12628917769    solar power generator   
723972  node/12628922141    solar power generator   
723973  node/12628922142    solar power generator   
723974  node/12628933024    solar power generator   

                                         geom  
0                POINT (8.5179932 49.0180318)  
1                POINT (0.5218841 51.8530108)  
2                POINT (8.8740961 53.0589349)  
3               POINT (11.5945844 48.1894386)  
4                POINT (9.9642052 53.5279202)  
...                                       ...  
723970          POINT (19.3732906 49.9230957)  
723971          POINT (19.3716505 49.9244208)  
723972          POINT (19.3361361 49.9016856)  
723973  POINT (19.3359857 49.901575199999996)  
723974          POINT (20.0109837 49.8862204)  

[723975 rows x 3 columns]

In [ ]:
# Convert to GeoDataFrame (optional)
gdf = gpd.GeoDataFrame(merged_data_use, geometry='geom')

# Save as a new Parquet file
output_file = "Energy/use/merged_all_data_new1.parquet"
gdf.to_parquet(output_file)

print(f"✅ Merged data saved to {output_file}")

✅ Merged data saved to Energy/use/merged_all_data_new1.parquet


In [ ]:
data_test_load = pd.read_parquet('Energy/use/merged_all_data.parquet')
data_test_load

id                 obj_type  \
0        node/7342664546  battery power generator   
1        node/8196015382  battery power generator   
2        node/8371124657  battery power generator   
3       node/10121875287  battery power generator   
4       node/10939320863  battery power generator   
...                  ...                      ...   
359227  node/12626013356    solar power generator   
359228  node/12626098973    solar power generator   
359229  node/12626120429    solar power generator   
359230  node/12628910410    solar power generator   
359231  node/12628925414    solar power generator   

                                                     geom  
0       b'\x01\x01\x00\x00\x00\xcc\x19\x9bg6\t!@\xde\x...  
1       b'\x01\x01\x00\x00\x005\xad\xb9HF\xb3\xe0?A\x9...  
2       b'\x01\x01\x00\x00\x00N\x1f&\x86\x89\xbf!@\xe8...  
3       b"\x01\x01\x00\x00\x00ol\xd1]m0'@\xce\xcc'\x86...  
4       b'\x01\x01\x00\x00\x00+D\xd1M\xac\xed#@\xea\xf...  
...                                                   ...  
359227  b'\x01\x01\x00\x00\x00tJ\x9b\x055\x17\r\xc0\x0...  
359228  b'\x01\x01\x00\x00\x00\xc4\xfb\xbb\x88\x00\x11...  
359229  b'\x01\x01\x00\x00\x00\xdc\x17+\xc5\xe9\xff\t\...  
359230  b'\x01\x01\x00\x00\x00\xc1\x1f~\xfe{\x10\xfe\x...  
359231  b'\x01\x01\x00\x00\x00n\xfdOY\xa8\x10\xfe\xbf\...  

[359232 rows x 3 columns]

In [ ]:
data_EV = pd.read_parquet("EV\ev.parquet")
data_EV['geom'] = data_EV['geometry'].apply(lambda x: loads(x))
data_EV['obj_type'] = 'EV charging station'
data_EV_use = pd.DataFrame(data_EV[['id','obj_type','geom']])
data_EV_use

id             obj_type                           geom
0          node/25397898  EV charging station   POINT (8.4310523 49.0211913)
1          node/33127962  EV charging station   POINT (8.2171862 48.7772382)
2          node/46332876  EV charging station   POINT (4.6271973 52.3593789)
3          node/60207254  EV charging station    POINT (7.765589 48.0430166)
4         node/257374474  EV charging station   POINT (3.8507969 51.0300676)
...                  ...                  ...                            ...
110776  node/12626375146  EV charging station  POINT (24.9112437 60.1989773)
110777  node/12626405094  EV charging station  POINT (15.6765466 48.4782692)
110778  node/12626433621  EV charging station  POINT (24.9056425 60.2075665)
110779  node/12626510463  EV charging station   POINT (9.3796997 51.4954275)
110780  node/12626544677  EV charging station   POINT (6.3698119 46.2663502)

[110781 rows x 3 columns]

In [ ]:
# Convert to GeoDataFrame (optional)
gdf = gpd.GeoDataFrame(data_EV_use, geometry='geom')

# Save as a new Parquet file
output_file = "EV/ev_all_data.parquet"
gdf.to_parquet(output_file)

print(f"✅ Merged data saved to {output_file}")

✅ Merged data saved to EV/ev_all_data.parquet


In [ ]:
data_Gr = pd.read_parquet("Land Greenery\greenery.parquet")
data_Gr['geom'] = data_Gr['geometry'].apply(lambda x: loads(x))
data_Gr

id               @id FIXME HE_ref  \
0           node/262696       node/262696  None   None   
1         node/12620081     node/12620081  None   None   
2         node/17025150     node/17025150  None   None   
3         node/25611999     node/25611999  None   None   
4         node/26944712     node/26944712  None   None   
...                 ...               ...   ...    ...   
16972  node/12625712107  node/12625712107  None   None   
16973  node/12625831936  node/12625831936  None   None   
16974  node/12625876729  node/12625876729  None   None   
16975  node/12625876730  node/12625876730  None   None   
16976  node/12626304959  node/12626304959  None   None   

      OnroerendErfgoed:criteria SIRUTA:code abandoned abandoned:shop access  \
0                          None        None      None           None   None   
1                          None        None      None           None   None   
2                          None        None      None           None   None   
3                          None        None      None           None   None   
4                          None        None      None           None   None   
...                         ...         ...       ...            ...    ...   
16972                      None        None      None           None   None   
16973                      None        None      None           None   None   
16974                      None        None      None           None   None   
16975                      None        None      None           None   None   
16976                      None        None      None           None   None   

      acres  ... wikimedia_commons wikipedia  wood wood:age wood:lost  \
0      None  ...              None      None  None     None      None   
1      None  ...              None      None  None     None      None   
2      None  ...              None      None  None     None      None   
3      None  ...              None      None  None     None      None   
4      None  ...              None      None  None     None      None   
...     ...  ...               ...       ...   ...      ...       ...   
16972  None  ...              None      None  None     None      None   
16973  None  ...              None      None  None     None      None   
16974  None  ...              None      None  None     None      None   
16975  None  ...              None      None  None     None      None   
16976  None  ...              None      None  None     None      None   

      wpt_description wpt_symbol  \
0                None       None   
1                None       None   
2                None       None   
3                None       None   
4                None       None   
...               ...        ...   
16972            None       None   
16973            None       None   
16974            None       None   
16975            None       None   
16976            None       None   

                                                geometry  \
0      b'\x01\x01\x00\x00\x00s~/*N\x9a\xe7\xbf\x91\x0...   
1      b'\x01\x01\x00\x00\x001\xe4}\xc1\x13_\xe3\xbf\...   
2      b'\x01\x01\x00\x00\x00\xb1\x03\x9d\xff\rX!@\x8...   
3      b'\x01\x01\x00\x00\x00\x7f_m\xd6*\x0b\xbc?W\xe...   
4      b'\x01\x01\x00\x00\x00\xe9\xd1TO\xe6\x1f\xc6\x...   
...                                                  ...   
16972  b'\x01\x01\x00\x00\x00Ga\xcd\xb7\xf4\xda8@z\x1...   
16973  b'\x01\x01\x00\x00\x00\x8b\x94\x1cf\x1ek@@\xc2...   
16974  b'\x01\x01\x00\x00\x00U\x13D\xdd\x07l@@\xdd\xe...   
16975  b'\x01\x01\x00\x00\x00\xaa\xe3B/\xedk@@G\x1a\x...   
16976  b'\x01\x01\x00\x00\x00dncXjv+@\xf3l\xfb\xc3;\x...   

                                           geometry_bbox  \
0      {'xmin': -0.7375862002372742, 'ymin': 51.10499...   
1      {'xmin': -0.6053561568260193, 'ymin': 52.18638...   
2      {'xmin': 8.671980857849121, 'ymin': 49.5445289...   
3      {'xmin': 0.10954538732767105, 'ymin': 52.24834...   
4      {'xmin': -0.17284852266311646, 'ymin'

In [ ]:
def categorize_node(row):
    if row['leisure'] in ['garden', 'park']:
        return row['leisure']
    elif row['natural'] in ['wood']:
        return 'forest'
    elif row['natural'] in ['tree_row']:
        return 'tree'
    elif row['landuse'] in ['flowerbed', 'grass', 'recreation_ground']:
        return row['landuse']
    else:
        return 'other greenery area'

In [ ]:
data_Gr['obj_type'] = data_Gr.apply(categorize_node, axis=1)
data_Gr_use = pd.DataFrame(data_Gr[['id','obj_type','geom']])
data_Gr_use

id obj_type                           geom
0           node/262696   forest  POINT (-0.7375861 51.1050004)
1         node/12620081   garden  POINT (-0.6053561 52.1863933)
2         node/17025150     park   POINT (8.6719818 49.5445307)
3         node/25611999     park    POINT (0.1095454 52.248354)
4         node/26944712   garden  POINT (-0.1728485 50.8393318)
...                 ...      ...                            ...
16972  node/12625712107     park  POINT (24.8552966 60.6141545)
16973  node/12625831936     park   POINT (32.8368652 39.933047)
16974  node/12625876729     park    POINT (32.84399 39.9257175)
16975  node/12625876730     park  POINT (32.8431758 39.9268834)
16976  node/12626304959     park  POINT (13.7312801 46.1815114)

[16977 rows x 3 columns]

In [ ]:
# Convert to GeoDataFrame (optional)
gdf = gpd.GeoDataFrame(data_Gr_use, geometry='geom')

# Save as a new Parquet file
output_file = "Land Greenery/use/gr_all_data.parquet"
gdf.to_parquet(output_file)

print(f"✅ Merged data saved to {output_file}")

✅ Merged data saved to Land Greenery/use/gr_all_data.parquet


In [ ]:
data_PT = pd.read_parquet("Public Transport\pubic_t.parquet")
data_PT['geom'] = data_PT['geometry'].apply(lambda x: loads(x))
data_PT['obj_type'] = 'public transport station'
data_PT

id               @id FIXME GTT:Revised HE_ref   HSR  \
0           node/104734       node/104734  None        None   None  None   
1           node/105105       node/105105  None        None   None  None   
2           node/223749       node/223749  None        None   None  None   
3           node/271281       node/271281  None        None   None  None   
4           node/271323       node/271323  None        None   None  None   
...                 ...               ...   ...         ...    ...   ...   
58654  node/12624445080  node/12624445080  None        None   None  None   
58655  node/12625428589  node/12625428589  None        None   None  None   
58656  node/12625592670  node/12625592670  None        None   None  None   
58657  node/12625592675  node/12625592675  None        None   None  None   
58658  node/12625853738  node/12625853738  None        None   None  None   

       IBNR JLT:zon LMCU:NOM_ARRET LMCU:OBJECTID  ... wp:it wpt_symbol  zone  \
0      None    None           None          None  ...  None       None  None   
1      None    None           None          None  ...  None       None  None   
2      None    None           None          None  ...  None       None  None   
3      None    None           None          None  ...  None       None  None   
4      None    None           None          None  ...  None       None  None   
...     ...     ...            ...           ...  ...   ...        ...   ...   
58654  None    None           None          None  ...  None       None  None   
58655  None    None           None          None  ...  None       None  None   
58656  None    None           None          None  ...  None       None  None   
58657  None    None           None          None  ...  None       None  None   
58658  None    None           None          None  ...  None       None  None   

      zone:Brupass zone:HSL zone:LSL  \
0             None     None     None   
1             None     None     None   
2             None     None     None   
3             None     None     None   
4             None     None     None   
...            ...      ...      ...   
58654         None     None     None   
58655         None     None     None   
58656         None     None     None   
58657         None     None     None   
58658         None     None     None   

                                                geometry  \
0      b'\x01\x01\x00\x00\x00\xadF\x1b\xec\xf2\x92\xf...   
1      b'\x01\x01\x00\x00\x00\x19a@\xe5N\x9f\x9b\xbf\...   
2      b'\x01\x01\x00\x00\x00\x90\x18\x98pC\xc5=@d\xf...   
3      b'\x01\x01\x00\x00\x00\xfb\x02\x1f(\\\x14\xf8\...   
4      b'\x01\x01\x00\x00\x00\x90\xdc\x9at[\xc2\xf9\x...   
...                                                  ...   
58654  b'\x01\x01\x00\x00\x00\x856J\xa8*\xce\x17@\xc0...   
58655  b'\x01\x01\x00\x00\x00\xf5\x03\r\xec\xe7c\xf8\...   
58656  b'\x01\x01\x00\x00\x00w\xd06H\xd2>A@\xdb\xe0\x...   
58657  b'\x01\x01\x00\x00\x00!\xd2\xca\x18z<A@@CI\x92...   
58658  b'\x01\x01\x00\x00\x00\x03\xc2\x98>\x85\xa51@\...   

                                           geometry_bbox  \
0      {'xmin': -1.7858763933181763, 'ymin': 51.56565...   
1      {'xmin': -0.026974903419613838, 'ymin': 52.053...   
2      {'xmin': 29.770557403564453, 'ymin': 59.984767...   
3      {'xmin': -1.504970908164978, 'ymin': 50.855041...   
4      {'xmin': -1.6099505424499512, 'ymin': 50.78470...   
...                                                  ...   
58654  {'xmin': 5.951334476470947, 'ymin': 46.5748176...   
58655  {'xmin': -1.5243912935256958, 'ymin': 55.10326...   
58656  {'xmin': 34.49079132080078, 'ymin': 50.5692939...   
58657  {'xmin': 34.47247314453125, 'ymin': 50.5796318...   
58658  {'xmin': 17.646562576293945, 'ymin': 59.858219...   

                                geom                  obj_type  
0      POINT (-1.7858762 51.5656526)  public transport station  
1      POINT (-0.0269749 52.0532089)  public transport station  
2      POINT (29.7705603 59.9

In [ ]:
data_PT_raw = pd.read_json("Public Transport/export_public_t_station.json")
data_PT_raw = pd.DataFrame(data_PT_raw['features'])
data_PT_raw

features
0      {'type': 'Feature', 'properties': {'@id': 'nod...
1      {'type': 'Feature', 'properties': {'@id': 'nod...
2      {'type': 'Feature', 'properties': {'@id': 'nod...
3      {'type': 'Feature', 'properties': {'@id': 'nod...
4      {'type': 'Feature', 'properties': {'@id': 'nod...
...                                                  ...
58654  {'type': 'Feature', 'properties': {'@id': 'nod...
58655  {'type': 'Feature', 'properties': {'@id': 'nod...
58656  {'type': 'Feature', 'properties': {'@id': 'nod...
58657  {'type': 'Feature', 'properties': {'@id': 'nod...
58658  {'type': 'Feature', 'properties': {'@id': 'nod...

[58659 rows x 1 columns]

In [ ]:
data_PT_raw.dtypes

features    object
dtype: object

In [ ]:
data_PT_raw['idraw'] = data_PT_raw['features'].apply(lambda x: x['properties']['@id'])
data_PT_raw['my_extended_data'] = data_PT_raw['features'].apply(lambda x: x['properties'])
data_PT_raw = data_PT_raw[['idraw','my_extended_data']]
data_PT_raw

idraw                                   my_extended_data
0           node/104734  {'@id': 'node/104734', 'addr:city': 'Swindon',...
1           node/105105  {'@id': 'node/105105', 'name': 'Royston', 'nap...
2           node/223749  {'@id': 'node/223749', 'amenity': 'ferry_termi...
3           node/271281  {'@id': 'node/271281', 'name': 'Beaulieu Road'...
4           node/271323  {'@id': 'node/271323', 'name': 'Sway', 'naptan...
...                 ...                                                ...
58654  node/12624445080  {'@id': 'node/12624445080', 'name': 'Gare de S...
58655  node/12625428589  {'@id': 'node/12625428589', 'name': 'Newsham S...
58656  node/12625592670  {'@id': 'node/12625592670', 'addr:housenumber'...
58657  node/12625592675  {'@id': 'node/12625592675', 'amenity': 'bus_st...
58658  node/12625853738  {'@id': 'node/12625853738', 'alt_name': 'Resec...

[58659 rows x 2 columns]

In [ ]:
data_PT_use = pd.merge(pd.DataFrame(data_PT[['id','obj_type','geom']]), data_PT_raw, how='left', left_on='id', right_on='idraw')
data_PT_use = data_PT_use[['id','obj_type','geom','my_extended_data']]
data_PT_use

id                  obj_type  \
0           node/104734  public transport station   
1           node/105105  public transport station   
2           node/223749  public transport station   
3           node/271281  public transport station   
4           node/271323  public transport station   
...                 ...                       ...   
58654  node/12624445080  public transport station   
58655  node/12625428589  public transport station   
58656  node/12625592670  public transport station   
58657  node/12625592675  public transport station   
58658  node/12625853738  public transport station   

                                geom  \
0      POINT (-1.7858762 51.5656526)   
1      POINT (-0.0269749 52.0532089)   
2      POINT (29.7705603 59.9847748)   
3      POINT (-1.5049707 50.8550478)   
4      POINT (-1.6099505 50.7847131)   
...                              ...   
58654   POINT (5.9513346 46.5748251)   
58655  POINT (-1.5243911 55.1032737)   
58656  POINT (34.4907923 50.5692956)   
58657  POINT (34.4724761 50.5796378)   
58658  POINT (17.6465644 59.8582208)   

                                        my_extended_data  
0      {'@id': 'node/104734', 'addr:city': 'Swindon',...  
1      {'@id': 'node/105105', 'name': 'Royston', 'nap...  
2      {'@id': 'node/223749', 'amenity': 'ferry_termi...  
3      {'@id': 'node/271281', 'name': 'Beaulieu Road'...  
4      {'@id': 'node/271323', 'name': 'Sway', 'naptan...  
...                                                  ...  
58654  {'@id': 'node/12624445080', 'name': 'Gare de S...  
58655  {'@id': 'node/12625428589', 'name': 'Newsham S...  
58656  {'@id': 'node/12625592670', 'addr:housenumber'...  
58657  {'@id': 'node/12625592675', 'amenity': 'bus_st...  
58658  {'@id': 'node/12625853738', 'alt_name': 'Resec...  

[58659 rows x 4 columns]

In [ ]:
data_PT_use = pd.DataFrame(data_PT[['id','obj_type','geom']])
data_PT_use

id                  obj_type  \
0           node/104734  public transport station   
1           node/105105  public transport station   
2           node/223749  public transport station   
3           node/271281  public transport station   
4           node/271323  public transport station   
...                 ...                       ...   
58654  node/12624445080  public transport station   
58655  node/12625428589  public transport station   
58656  node/12625592670  public transport station   
58657  node/12625592675  public transport station   
58658  node/12625853738  public transport station   

                                geom  
0      POINT (-1.7858762 51.5656526)  
1      POINT (-0.0269749 52.0532089)  
2      POINT (29.7705603 59.9847748)  
3      POINT (-1.5049707 50.8550478)  
4      POINT (-1.6099505 50.7847131)  
...                              ...  
58654   POINT (5.9513346 46.5748251)  
58655  POINT (-1.5243911 55.1032737)  
58656  POINT (34.4907923 50.5692956)  
58657  POINT (34.4724761 50.5796378)  
58658  POINT (17.6465644 59.8582208)  

[58659 rows x 3 columns]

In [ ]:
# Convert to GeoDataFrame (optional)
gdf = gpd.GeoDataFrame(data_PT_use, geometry='geom')

# Save as a new Parquet file
output_file = "Public Transport/use/pt_all_data.parquet"
gdf.to_parquet(output_file)

print(f"✅ Merged data saved to {output_file}")

✅ Merged data saved to Public Transport/use/pt_all_data.parquet


In [ ]:
data_Rc = pd.read_parquet("Recycling\\recycling.parquet")
data_Rc['geom'] = data_Rc['geometry'].apply(lambda x: loads(x))
data_Rc

id               @id FIXME  TODO access  \
0         node/20944608     node/20944608  None  None   None   
1         node/26066489     node/26066489  None  None   None   
2         node/26066525     node/26066525  None  None   None   
3         node/26209296     node/26209296  None  None   None   
4         node/26209297     node/26209297  None  None   None   
...                 ...               ...   ...   ...    ...   
85829  node/12628343471  node/12628343471  None  None   None   
85830  node/12628723501  node/12628723501  None  None   None   
85831  node/12628735121  node/12628735121  None  None   None   
85832  node/12628735122  node/12628735122  None  None   None   
85833  node/12629315013  node/12629315013  None  None   None   

      access:conditional addr:city addr:city:simc addr:conscriptionnumber  \
0                   None      None           None                    None   
1                   None      None           None                    None   
2                   None      None           None                    None   
3                   None      None           None                    None   
4                   None      None           None                    None   
...                  ...       ...            ...                     ...   
85829               None      None           None                    None   
85830               None      None           None                    None   
85831               None      None           None                    None   
85832               None      None           None                    None   
85833               None      None           None                    None   

      addr:country  ... wheelchair:description width wikimedia_commons  \
0             None  ...                   None  None              None   
1             None  ...                   None  None              None   
2             None  ...                   None  None              None   
3             None  ...                   None  None              None   
4             None  ...                   None  None              None   
...            ...  ...                    ...   ...               ...   
85829         None  ...                   None  None              None   
85830         None  ...                   None  None              None   
85831         None  ...                   None  None              None   
85832         None  ...                   None  None              None   
85833         None  ...                   None  None              None   

      wikipedia  wood wpt_description wpt_symbol  \
0          None  None            None       None   
1          None  None            None       None   
2          None  None            None       None   
3          None  None            None       None   
4          None  None            None       None   
...         ...   ...             ...        ...   
85829      None  None            None       None   
85830      None  None            None       None   
85831      None  None            None       None   
85832      None  None            None       None   
85833      None  None            None       None   

                                                geometry  \
0      b'\x01\x01\x00\x00\x00[\xee\xcc\x04\xc3E)@\xdf...   
1      b'\x01\x01\x00\x00\x00\r6u\x1e\x15\x9f\x1a@\x8...   
2      b'\x01\x01\x00\x00\x00\x05p\x0e2$\x92\x1a@\xc2...   
3      b'\x01\x01\x00\x00\x00\xe1\xd9yvT\xac#@%\x9b\x...   
4      b'\x01\x01\x00\x00\x00\xff:\xdc\xb3S\xb0#@-b3\...   
...                                                  ...   
85829  b'\x01\x01\x00\x00\x00\xfb\x92\x8d\x07[\xe8+@\...   
85830  b'\x01\x01\x00\x00\x00T\xd9\xc1\xd2\n\xc5\x18@...   
85831  b'\x01\x01\x00\x00\x00\xa5\xc3\x9e\xd1\xb1\x1a...   
85832  b'\x01\x01\x00\x00\x00x\x14\x9d\x1b\x89\x1a-@)...   
85833  b"\x01\x01\x00\x00\x00\xa5\xe87\x02\xa7\xf1'@\...   

                                           geometry_bbox  \
0      {'xmin': 12.6362533569335

In [ ]:
data_Rc['obj_type'] = 'waste recycle facility'
data_Rc_use = pd.DataFrame(data_Rc[['id','obj_type','geom']])
data_Rc_use

id                obj_type                           geom
0         node/20944608  waste recycle facility  POINT (12.6362535 55.6571437)
1         node/26066489  waste recycle facility    POINT (6.655354 51.4405287)
2         node/26066525  waste recycle facility   POINT (6.6427162 51.4507804)
3         node/26209296  waste recycle facility   POINT (9.8365819 52.2240181)
4         node/26209297  waste recycle facility   POINT (9.8443886 52.2245821)
...                 ...                     ...                            ...
85829  node/12628343471  waste recycle facility  POINT (13.9538195 50.1473361)
85830  node/12628723501  waste recycle facility   POINT (6.1924241 51.0619215)
85831  node/12628735121  waste recycle facility  POINT (14.5521379 50.0648706)
85832  node/12628735122  waste recycle facility  POINT (14.5518273 50.0650073)
85833  node/12629315013  waste recycle facility  POINT (11.9719773 50.9741364)

[85834 rows x 3 columns]

In [ ]:
# Convert to GeoDataFrame (optional)
gdf = gpd.GeoDataFrame(data_Rc_use, geometry='geom')

# Save as a new Parquet file
output_file = "Recycling/use/rc_all_data.parquet"
gdf.to_parquet(output_file)

print(f"✅ Merged data saved to {output_file}")

✅ Merged data saved to Recycling/use/rc_all_data.parquet


In [ ]:
data = pd.read_parquet("Public Transport\\use\\pt_all_data.parquet")
data

id                  obj_type  \
0           node/104734  public transport station   
1           node/105105  public transport station   
2           node/223749  public transport station   
3           node/271281  public transport station   
4           node/271323  public transport station   
...                 ...                       ...   
58654  node/12624445080  public transport station   
58655  node/12625428589  public transport station   
58656  node/12625592670  public transport station   
58657  node/12625592675  public transport station   
58658  node/12625853738  public transport station   

                                                    geom  \
0      b'\x01\x01\x00\x00\x00\xadF\x1b\xec\xf2\x92\xf...   
1      b'\x01\x01\x00\x00\x00\x19a@\xe5N\x9f\x9b\xbf\...   
2      b'\x01\x01\x00\x00\x00\x90\x18\x98pC\xc5=@d\xf...   
3      b'\x01\x01\x00\x00\x00\xfb\x02\x1f(\\\x14\xf8\...   
4      b'\x01\x01\x00\x00\x00\x90\xdc\x9at[\xc2\xf9\x...   
...                                                  ...   
58654  b'\x01\x01\x00\x00\x00\x856J\xa8*\xce\x17@\xc0...   
58655  b'\x01\x01\x00\x00\x00\xf5\x03\r\xec\xe7c\xf8\...   
58656  b'\x01\x01\x00\x00\x00w\xd06H\xd2>A@\xdb\xe0\x...   
58657  b'\x01\x01\x00\x00\x00!\xd2\xca\x18z<A@@CI\x92...   
58658  b'\x01\x01\x00\x00\x00\x03\xc2\x98>\x85\xa51@\...   

                                                    prop  
0      {'@id': 'node/104734', 'FIXME': None, 'GTT:Rev...  
1      {'@id': 'node/105105', 'FIXME': None, 'GTT:Rev...  
2      {'@id': 'node/223749', 'FIXME': None, 'GTT:Rev...  
3      {'@id': 'node/271281', 'FIXME': None, 'GTT:Rev...  
4      {'@id': 'node/271323', 'FIXME': None, 'GTT:Rev...  
...                                                  ...  
58654  {'@id': 'node/12624445080', 'FIXME': None, 'GT...  
58655  {'@id': 'node/12625428589', 'FIXME': None, 'GT...  
58656  {'@id': 'node/12625592670', 'FIXME': None, 'GT...  
58657  {'@id': 'node/12625592675', 'FIXME': None, 'GT...  
58658  {'@id': 'node/12625853738', 'FIXME': None, 'GT...  

[58659 rows x 4 columns]

In [ ]:
data = data.rename(columns={"prop": "extended_information"})
data['geom'] = data['geom'].apply(lambda x: loads(x))
data

id                  obj_type  \
0           node/104734  public transport station   
1           node/105105  public transport station   
2           node/223749  public transport station   
3           node/271281  public transport station   
4           node/271323  public transport station   
...                 ...                       ...   
58654  node/12624445080  public transport station   
58655  node/12625428589  public transport station   
58656  node/12625592670  public transport station   
58657  node/12625592675  public transport station   
58658  node/12625853738  public transport station   

                                geom  \
0      POINT (-1.7858762 51.5656526)   
1      POINT (-0.0269749 52.0532089)   
2      POINT (29.7705603 59.9847748)   
3      POINT (-1.5049707 50.8550478)   
4      POINT (-1.6099505 50.7847131)   
...                              ...   
58654   POINT (5.9513346 46.5748251)   
58655  POINT (-1.5243911 55.1032737)   
58656  POINT (34.4907923 50.5692956)   
58657  POINT (34.4724761 50.5796378)   
58658  POINT (17.6465644 59.8582208)   

                                    extended_information  
0      {'@id': 'node/104734', 'FIXME': None, 'GTT:Rev...  
1      {'@id': 'node/105105', 'FIXME': None, 'GTT:Rev...  
2      {'@id': 'node/223749', 'FIXME': None, 'GTT:Rev...  
3      {'@id': 'node/271281', 'FIXME': None, 'GTT:Rev...  
4      {'@id': 'node/271323', 'FIXME': None, 'GTT:Rev...  
...                                                  ...  
58654  {'@id': 'node/12624445080', 'FIXME': None, 'GT...  
58655  {'@id': 'node/12625428589', 'FIXME': None, 'GT...  
58656  {'@id': 'node/12625592670', 'FIXME': None, 'GT...  
58657  {'@id': 'node/12625592675', 'FIXME': None, 'GT...  
58658  {'@id': 'node/12625853738', 'FIXME': None, 'GT...  

[58659 rows x 4 columns]

In [ ]:
# Convert to GeoDataFrame (optional)
gdf = gpd.GeoDataFrame(data, geometry='geom')

# Save as a new Parquet file
output_file = "Public Transport/use/pt_all_data_new.parquet"
gdf.to_parquet(output_file)

print(f"✅ Merged data saved to {output_file}")

✅ Merged data saved to Public Transport/use/pt_all_data_new.parquet
